In [1]:
from DPOD.datasets.linemod.models_handler import read_obj_file
import numpy as np
from glob import glob

# Core functions

In [2]:
def process_face(vertices, face, max_dist=0.01):
    v_face = vertices[face, :]
    h_diff = v_face[:, 0].max() - v_face[:, 0].min()
    w_diff = v_face[:, 1].max() - v_face[:, 1].min()
    z_diff = v_face[:, 2].max() - v_face[:, 2].min()
    diff = max(h_diff, w_diff, z_diff)
    if -1 in face:
        print("elo")
    if diff > max_dist:
        mids = np.stack([v_face[[2, 1]].mean(axis=0), 
                         v_face[[0, 2]].mean(axis=0), 
                         v_face[[0, 1]].mean(axis=0)])
        mids_ids = [len(vertices) + i for i in range(3)]
        vertices = np.concatenate([vertices, mids])
        faces = []
        for i in range(3):
            vertices, new_faces = process_face(
                vertices, 
                np.array([face[i], mids_ids[(i+1)%3], mids_ids[(i+2)%3]]),
                max_dist,
            )
            faces += new_faces
        vertices, new_faces = process_face(vertices, mids_ids, max_dist)
        faces += new_faces

    else:
        faces = [face]
    
    return vertices, faces

In [3]:
def save_obj_file(filename, ver, facs):
    with open(filename, "w") as file:
        for v in ver:
            file.write(f"v {v[0]} {v[1]} {v[2]}\n")
            
        for f in facs:
            file.write(f"f {f[0]} {f[1]} {f[2]}\n")

In [4]:
def check_accuracy(vertices, facs):
    max_diff = 0
    for face in facs:
        v_face = vertices[face, :]
        h_diff = v_face[:, 0].max() - v_face[:, 0].min()
        w_diff = v_face[:, 1].max() - v_face[:, 1].min()
        z_diff = v_face[:, 2].max() - v_face[:, 2].min()
        diff = max(h_diff, w_diff, z_diff)
        if diff > max_diff:
            max_diff = diff
    return max_diff

# Testing

In [5]:
ver, facs = read_obj_file("models_small/Duck/007_small.obj")
check_accuracy(ver, facs)

0.027608

In [6]:
faces = []
for face in facs:
    ver, new_faces = process_face(ver, face)
    faces += new_faces
print(ver.shape, np.array(faces).shape)
print(np.array(faces).min(), np.array(faces).max())

(1321, 3) (1819, 3)
0 1320


In [7]:
len(ver), check_accuracy(ver, faces)

(1321, 0.009998)

In [8]:
save_obj_file("test.obj", ver, facs)

# Generate big models

In [5]:
import os
from tqdm.notebook import tqdm

DIRECTORY_NAME = "models_001m"
max_dist = 0.001

for model_dir in tqdm(glob(f'models_small/*')):
    model_name = os.path.split(model_dir)[1]
    if 'Holepuncher' in model_dir:
        continue
    model_filepath = glob(f'{model_dir}/*.obj')[0]
    ver, facs = read_obj_file(model_filepath)
    faces = []
    for face in facs:
        ver, new_faces = process_face(ver, face, max_dist)
        faces += new_faces
    os.makedirs(f"{DIRECTORY_NAME}/{model_dir.split('/')[1]}", exist_ok=True)
    save_obj_file(f"{DIRECTORY_NAME}/{model_dir.split('/')[1]}/001.obj", ver, np.array(faces) + 1)

In [10]:
ver, facs = read_obj_file(f"{DIRECTORY_NAME}/Driller/001.obj")
print(ver.shape, facs.shape)

(28366, 3) (28864, 3)


In [11]:
print(check_accuracy(ver, facs))

0.004997750000000009


## Generate reversed_mapping using new approach

In [12]:
import os
from tqdm.notebook import tqdm
import numpy as np
from DPOD.datasets.linemod.models_handler import ModelsHandler
from DPOD.datasets.linemod.models_handler import get_reversed_mapping
from glob import glob


mh = ModelsHandler()
for model_dir in glob(f'models_small/*'):
    model_name = os.path.split(model_dir)[1]
    if 'Holepuncher' in model_dir:
        continue
    mapping = get_reversed_mapping(mh, model_name)
    
    os.makedirs(f"{DIRECTORY_NAME}/{model_name}", exist_ok=True)
    np.save(f"{DIRECTORY_NAME}/{model_name}/mapping.npy", mapping)
    print(f"Done {model_name}")

  0%|          | 94/65025 [00:00<01:30, 718.75it/s]

{'Ape': 1, 'Can': 2, 'Cat': 3, 'Driller': 4, 'Duck': 5, 'Eggbox': 6, 'Glue': 7}


  0%|          | 75/65025 [00:00<02:28, 436.07it/s]

Done Ape



  5%|▍         | 3016/65025 [00:07<08:33, 120.80it/s]


...

 95%|█████████▌| 62032/65025 [06:09<00:36, 81.08it/s]





 95%|█████████▌| 62035/65025 [06:09<00:36, 81.08it/s]





 95%|█████████▌| 62052/65025 [06:09<00:38, 77.40it/s]





 95%|█████████▌| 62061/65025 [06:09<00:39, 74.78it/s]





 95%|█████████▌| 62061/65025 [06:09<00:39, 74.78it/s]





 95%|█████████▌| 62061/65025 [06:09<00:39, 74.78it/s]





 95%|█████████▌| 62062/65025 [06:09<00:39, 74.78it/s]





 95%|█████████▌| 62065/65025 [06:10<00:39, 74.78it/s]





 95%|█████████▌| 62068/65025 [06:10<00:39, 74.78it/s]





 95%|█████████▌| 62088/65025 [06:10<00:41, 71.63it/s]





 95%|█████████▌| 62088/65025 [06:10<00:41, 71.63it/s]





 95%|█████████▌| 62088/65025 [06:10<00:41, 71.63it/s]





 95%|█████████▌| 62088/65025 [06:10<00:41, 71.63it/s]





 95%|█████████▌| 62090/65025 [06:10<00:40, 71.63it/s]





 95%|█████████▌| 62096/65025 [06:10<00:40, 71.63it/s]





 95%|█████████▌| 62097/65025 [06:10<00:40, 71.63it/s]





 96%|█████████▌| 62103/65025 [06:10<00:40, 71.63it/s]




 97%|█████████▋| 63127/65025 [06:16<00:23, 81.46it/s]





 97%|█████████▋| 63130/65025 [06:17<00:23, 81.46it/s]





 97%|█████████▋| 63145/65025 [06:17<00:23, 81.49it/s]





 97%|█████████▋| 63151/65025 [06:17<00:21, 85.48it/s]





 97%|█████████▋| 63152/65025 [06:17<00:21, 85.48it/s]





 97%|█████████▋| 63155/65025 [06:17<00:21, 85.48it/s]





 97%|█████████▋| 63156/65025 [06:17<00:21, 85.48it/s]





 97%|█████████▋| 63159/65025 [06:17<00:21, 85.48it/s]





 97%|█████████▋| 63165/65025 [06:17<00:21, 85.48it/s]





 97%|█████████▋| 63185/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63186/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63188/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63190/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63191/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63196/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63201/65025 [06:17<00:23, 79.23it/s]





 97%|█████████▋| 63214/65025 [06:17<00:24, 73.69it/s]




 99%|█████████▉| 64283/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64283/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64284/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64285/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64291/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64292/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64295/65025 [06:23<00:07, 92.80it/s]





 99%|█████████▉| 64308/65025 [06:23<00:07, 90.01it/s]





 99%|█████████▉| 64311/65025 [06:23<00:08, 88.02it/s]





 99%|█████████▉| 64325/65025 [06:24<00:07, 89.44it/s]





 99%|█████████▉| 64328/65025 [06:24<00:07, 93.62it/s]





 99%|█████████▉| 64330/65025 [06:24<00:07, 93.62it/s]





 99%|█████████▉| 64332/65025 [06:24<00:07, 93.62it/s]





 99%|█████████▉| 64351/65025 [06:24<00:07, 95.71it/s]





 99%|█████████▉| 64351/65025 [06:24<00:07, 95.71it/s]





 99%|█████████▉| 64352/65025 [06:24<00:07, 95.71it/s]





 99%|█████████▉| 64355/65025 [06:24<00:07, 95.71it/s]




Done Driller








100%|██████████| 65025/65025 [06:39<00:00, 155.80it/s]